In [ ]:
from bs4 import BeautifulSoup as bs4
import requests
import pandas as pd
import re
import time
from selenium import webdriver
from selenium.webdriver.common.keys import Keys

from webdriver_manager.chrome import ChromeDriverManager

from fake_useragent import UserAgent

import nltk
nltk.download("punkt")

pages = [
    "https://www.noticiasaominuto.com/politica",
    "https://www.noticiasaominuto.com/economia",
    "https://www.noticiasaominuto.com/desporto",
    "https://www.noticiasaominuto.com/pais",
    "https://www.noticiasaominuto.com/mundo",
]

In [2]:
driver = webdriver.Chrome(ChromeDriverManager().install())

[WDM] - Downloading: 100%|██████████| 6.30M/6.30M [00:01<00:00, 3.76MB/s]


In [3]:
# Open webpage to reject cookies and maximize window
driver.get("https://www.noticiasaominuto.com/politica")

In [7]:
urls = set()
for page in pages:
    print("------------")
    print(page)
    print("------------")
    # Open webpage
    driver.get(page)
    
    time.sleep(3)

    # Scroll down until the end of the page
    lenOfPage = driver.execute_script("window.scrollTo(0, document.body.scrollHeight);var lenOfPage=document.body.scrollHeight;return lenOfPage;")
    match=False
    while(match==False):
            lastCount = lenOfPage
            time.sleep(3)
            lenOfPage = driver.execute_script("window.scrollTo(0, document.body.scrollHeight);var lenOfPage=document.body.scrollHeight;return lenOfPage;")
            if lastCount==lenOfPage:
                match=True
    
    soup = bs4(driver.page_source, 'html.parser')
    links = soup.find_all("p", class_ = "article-thumb-text")
    for link in links:
        urls.add(link.find("a")['href'])
        print(link.find("a")['href'])

------------
https://www.noticiasaominuto.com/politica
------------
https://www.noticiasaominuto.com/politica/2366212/melo-diz-que-psd-e-cds-nao-devem-fazer-acordos-com-chega-e-il-na-madeira
https://www.noticiasaominuto.com/politica/2366098/pan-quer-garantir-que-morte-de-animais-em-santo-tirso-nao-se-repete
https://www.noticiasaominuto.com/politica/2366126/governo-tem-de-fazer-a-sua-parte-para-dar-condicoes-dignas-a-imigrantes
https://www.noticiasaominuto.com/politica/2366027/be-quer-que-camara-do-porto-assuma-como-prioridade-manutencao-do-stop
https://www.noticiasaominuto.com/politica/2365704/be-questiona-cravinho-sobre-detencao-de-portugues-na-turquia
https://www.noticiasaominuto.com/politica/2365670/estado-da-nacao-e-bem-melhor-do-que-o-estado-da-oposicao
https://www.noticiasaominuto.com/desporto/2361072/para-ver-e-apostar-os-jogos-que-vao-marcar-a-semana
https://www.noticiasaominuto.com/politica/2365660/partidos-na-mira-da-justica-ps-nao-tem-razoes-para-estar-preocupado
https://www

In [18]:
len(urls) #284

2447

In [9]:
urls_test = [
    "https://www.noticiasaominuto.com/politica/2361729/andre-ventura-acusa-psd-e-ps-de-conluio-para-condicionar-a-justica",
]

In [19]:
texts=[]
sources=[]
df_urls = []
# Initialize an empty dataframe
df = pd.DataFrame(columns=['Text', 'Source', 'URL'])

for url in urls:
    # if url.split("https://expresso.pt")[1] == "":
    #     url = "https://expresso.pt" + url.split("https://expresso.pt")[2]
    print("-------------")
    print(url)
    print("-------------")
    text = "NONE"
    source = "SOL"
    #exclusive_article = False

    try:
        driver.get(url)

        soup = bs4(driver.page_source, 'html.parser')

        title_1 = soup.find("h1", class_ = "news-headline article-title").get_text().strip()
        title_2 = soup.find("h2", class_ = "news-subheadline").get_text().strip()
        #print(title_1)
        #print(title_2)
        body_elem = soup.find("div", class_ = "news-main-text content")
        paragraphs = body_elem.find_all("p")
        #print(paragraphs)
        text = ""
        for paragraph in paragraphs:
            #print(paragraph.get_text().strip())
            text += "\n" + paragraph.get_text().strip()
        lowercase_text = text.lower()
        #print(lowercase_text)
        if 'leia também:' in lowercase_text:
            index = lowercase_text.index('leia também:')
            news_text = text[:index]
            #print(news_text)

        text = title_1 + "\n" + title_2 + "\n" + news_text
        text = re.sub(r'\n+', '\n', text) # Replace consecutive paragraphs with a single one
        text = text.strip()

    except:
        pass
    
    texts.append(text)
    sources.append(source)
    df_urls.append(url)

    print(text)
    print(source)

    time.sleep(3)
        
# Create a new dataframe from the lists
new_data = pd.DataFrame({'Text': texts, 'Source': sources, 'URL': df_urls})

# Concatenate the new dataframe with the existing dataframe
df = pd.concat([df, new_data], ignore_index=True)

-------------
https://www.noticiasaominuto.com/pais/2365991/autarca-de-montalegre-da-nao-claro-e-inequivoco-a-exploracao-de-litio
-------------
Autarca de Montalegre dá "não claro e inequívoco" à exploração de lítio
A presidente da Câmara de Montalegre, Fátima Fernandes, assumiu hoje uma posição de um "não claro e inequívoco" à exploração de lítio no concelho, classificando o projeto como "danoso" para o concelho.
"É evidente que os interesses gerais do concelho não estão acautelados e não existem perspetivas inequívocas de que venham a ser tidos em conta de forma cabal e objetiva", afirmou a autarca, através de um comunicado que visa esclarecer a sua posição sobre a exploração de lítio projetada para o município do Norte do distrito de Vila Real.
A reformulação do projeto "Concessão de Exploração de Depósitos Minerais de Lítio e Minerais Associados - Romano", da empresa Lusorecursos, encontra-se em consulta pública desde o dia 27 de junho e até à próxima segunda-feira, dia 24 de julho

In [20]:
len(urls)

2447

In [21]:
len(texts)

2447

In [22]:
len(sources)

2447

In [23]:
len(df_urls)

2447

In [24]:
for url in df_urls:
    print(url)

https://www.noticiasaominuto.com/pais/2365991/autarca-de-montalegre-da-nao-claro-e-inequivoco-a-exploracao-de-litio
https://www.noticiasaominuto.com/economia/2360333/governo-britanico-aceita-aumentar-salarios-da-funcao-publica-ate-7
https://www.noticiasaominuto.com/pais/2363557/dois-feridos-graves-em-despiste-de-carro-contra-arvore-em-pegoes
https://www.noticiasaominuto.com/pais/2363258/covid-19-houve-ilegalidades-nos-apoios-do-governo-da-madeira-as-empresas
https://www.noticiasaominuto.com/desporto/2366083/ainda-temos-de-fazer-muitas-mudancas
https://www.noticiasaominuto.com/pais/2364572/portugal-mostra-melhoria-em-indicadores-de-objetivos-do-desenvolvimento
https://www.noticiasaominuto.com/economia/2365557/servico-da-divida-custa-mais-de-2000-milhoes-a-mocambique-em-2023
https://www.noticiasaominuto.com/mundo/2364381/bombeiro-morre-e-3-sofrem-ferimentos-apos-ficarem-presos-durante-incendio
https://www.noticiasaominuto.com/mundo/2365497/esfaqueia-o-proprio-irmao-apos-discussao-em-madr

In [25]:
df.head()

Text Source  \
0  Autarca de Montalegre dá "não claro e inequívo...    SOL   
1  Governo britânico aceita aumentar salários da ...    SOL   
2  Dois feridos graves em despiste de carro contr...    SOL   
3  Covid-19? Houve ilegalidades nos apoios do Gov...    SOL   
4  "Ainda temos de fazer muitas mudanças"\nO PSG ...    SOL   

                                                 URL  
0  https://www.noticiasaominuto.com/pais/2365991/...  
1  https://www.noticiasaominuto.com/economia/2360...  
2  https://www.noticiasaominuto.com/pais/2363557/...  
3  https://www.noticiasaominuto.com/pais/2363258/...  
4  https://www.noticiasaominuto.com/desporto/2366...

In [26]:
df.head()
df.to_csv("Noticias_ao_minuto_dataset.csv", index=False)

In [27]:
loaded_df = pd.read_csv("Noticias_ao_minuto_dataset.csv")
loaded_df.head()

Text Source  \
0  Autarca de Montalegre dá "não claro e inequívo...    SOL   
1  Governo britânico aceita aumentar salários da ...    SOL   
2  Dois feridos graves em despiste de carro contr...    SOL   
3  Covid-19? Houve ilegalidades nos apoios do Gov...    SOL   
4  "Ainda temos de fazer muitas mudanças"\nO PSG ...    SOL   

                                                 URL  
0  https://www.noticiasaominuto.com/pais/2365991/...  
1  https://www.noticiasaominuto.com/economia/2360...  
2  https://www.noticiasaominuto.com/pais/2363557/...  
3  https://www.noticiasaominuto.com/pais/2363258/...  
4  https://www.noticiasaominuto.com/desporto/2366...

In [28]:
for source in set(loaded_df['Source']):
    print(source)

SOL


In [29]:
num_rows_with_none = len(loaded_df[loaded_df['Text'] == 'NONE'])
print(num_rows_with_none)

0


In [30]:
len(loaded_df)

2447

In [31]:
final_dataset = df[df["Text"] != "NONE"]

In [32]:
len(final_dataset)

2447

In [33]:
final_dataset.head()
final_dataset.to_csv("Noticias_ao_minuto_dataset.csv", index=False)